In [33]:
from torch.utils.data import Dataset
import torch
from torchvision import transforms
from PIL import Image
import skimage.io
import numpy as np
import pandas as pd
import pretrainedmodels
from torch.utils.data import DataLoader
import time
import glob
import os
from multiprocessing import Pool
from transforms import *
from torch import nn

# Model Configs

In [34]:
model_configs = {'polynet':{
                   'input_size': 331,
                   'input_mean': [0.485, 0.456, 0.406, 0.406],
                   'input_std' : [0.229, 0.224, 0.225, 0.225]
                    },
                 'resnet34':{
                   'input_size': 224,
                   'input_mean': [0.485, 0.456, 0.406, 0.406],
                   'input_std' : [0.229, 0.224, 0.225, 0.225]
                    },
                 'senet154':{
                   'input_size': 224,
                   'input_mean': [0.485, 0.456, 0.406, 0.406],
                   'input_std' : [0.229, 0.224, 0.225, 0.225]
                    },
                 'nasnetamobile':{
                   'input_size': 224,
                   'input_mean': [0.5],
                   'input_std' : [0.5]
                    },
                 'inceptionresnetv2':{
                   'input_size': 299,
                   'input_mean': [0.5],
                   'input_std' : [0.5]
                    },
                 'inceptionv4':{
                   'input_size': 299,
                   'input_mean': [0.5],
                   'input_std' : [0.5]
                    },
                 'xception':{
                   'input_size': 299,
                   'input_mean': [0.5],
                   'input_std' : [0.5]
                    }
                }

# Dataset

In [35]:
class AtlasData(Dataset):
    def __init__(self, split, train = True, model = 'bninception'):
        self.split = split
        self.train = train
        self.train_str = 'train' if self.train else 'test'
        self.text_file = 'data/atlas_{}_split_{}.txt'.format(self.train_str, self.split)
        
        self.data = [[y for y in x.strip().split(' ')] for x in open(self.text_file, 'r').readlines()]
        self.imgs = [x[0] for x in self.data]
        self.labels = [[int(p) for p in x[1:]] for x in self.data]
        
        self.input_size = model_configs[model]['input_size']
        self.input_mean = model_configs[model]['input_mean']
        self.input_std = model_configs[model]['input_std']
        
        self.transforms = transforms.Compose([#GroupRandomRotate(360),
                                              GroupScale(self.input_size),
                                              Stack(roll=False),
                                              ToTorchFormatTensor(div=True),
                                              transforms.Normalize(self.input_mean, self.input_std),
                                            ])
        
    
    
    
    def load_image_stack(self, image_id):
        colors = ['red', 'green', 'blue', 'yellow']
        absolute_paths = ["data/train/{}_{}.png".format(image_id, color) for color in colors]
        images = [Image.open(path).convert('L') for path in absolute_paths]
        
        return images
    
    def __getitem__(self, i):
        image_id = self.imgs[i]
        image = self.load_image_stack(image_id)
        image = self.transforms(image)
        
        label = self.labels[i]
        label_arr = np.zeros(28, dtype = np.float32)
        [np.put(label_arr, x, 1) for x in label]
        
        label_arr = torch.from_numpy(label_arr)
        
        return image, label_arr, label
        
    def __len__(self):
        return len(self.imgs)
    
class EvalAtlasData(Dataset):
    def __init__(self, model):
        self.image_ids = sorted(set([x.split('_')[0] for x in os.listdir('data/test')]))
        
        self.input_size = model_configs[model]['input_size']
        self.input_mean = model_configs[model]['input_mean']
        self.input_std = model_configs[model]['input_std']
        
        self.transforms = transforms.Compose([GroupScale(self.input_size),
                                              Stack(roll=False),
                                              ToTorchFormatTensor(div=True),
                                              transforms.Normalize(self.input_mean, self.input_std),
                                            ])
        
    def load_image_stack(self, image_id):
        colors = ['red', 'green', 'blue', 'yellow']
        absolute_paths = ["data/test/{}_{}.png".format(image_id, color) for color in colors]
        images = [Image.open(path).convert('L') for path in absolute_paths]
        
        return images
    
    def __len__(self):
        return len(self.image_ids)
        
    def __getitem__(self, i):
        image_id = self.image_ids[i]
        images = self.load_image_stack(image_id)
        image = self.transforms(images)
            
        return image_id, image


# Generate Predictions to CSV

In [36]:
from torch.nn import Softmax
from sklearn.metrics import f1_score

softmax = Softmax()

def generate_preds(model_name,threshold,suffix):
    model = pretrainedmodels.__dict__[model_name](num_classes = 1000, pretrained = 'imagenet')
    in_features = model.last_linear.in_features
    model.last_linear = torch.nn.Linear(in_features, 28)
    
    if model_name == 'polynet':
        model = torch.nn.DataParallel(model, device_ids = [0,1,2,3]).cuda()
        model.load_state_dict(torch.load('{}_0.pth.tar'.format(model_name))['state_dict'])
        model = model.eval()
    else:
        model.load_state_dict(torch.load('{}_0.pth.tar'.format(model_name))['state_dict'])
        model = model.eval()
        model.cuda()

    eval_data = EvalAtlasData(model = model_name)
    dataloader = DataLoader(eval_data, 1, False)
    
    preds = []
    for i, (image_id, images) in enumerate(dataloader):
        images = images.cuda()

        raw_predictions = (model(images))
        
        predictions = np.argwhere(raw_predictions.data[0] > threshold)
        try:
            num_predictions = len(predictions.data[0])
        except IndexError:
            num_predictions = 0

        print('-----------------------------------------------------')
        print(image_id[0])
        print('Raw Prediction', raw_predictions)
        if num_predictions == 0:
            print('No value passed the threshold')
            predictions = [np.argmax(raw_predictions.detach().cpu().numpy())]
            num_predictions = 1
            print("Prediction:", predictions)
            print("Number of predictions", num_predictions)
        else:
            predictions = predictions.data[0].tolist()
            print("Prediction:", predictions)
            print("Number of predictions", num_predictions)

        predicted = ' '.join('%d' % prediction for prediction in predictions)
        print(image_id[0])
        print(predicted)
        pred = dict(Id = image_id[0], Predicted = predicted)
        preds.append(pred)
        
    df = pd.DataFrame(preds)
    df.to_csv('{}_{}_{}.csv'.format(model_name, threshold, suffix), index = False)
    


# Validate

In [81]:
def construct_rgby_model(model):
    modules = list(model.modules())
    first_conv_idx = list(filter(lambda x: isinstance(modules[x], nn.Conv2d), list(range(len(modules)))))[0]
    conv_layer = modules[first_conv_idx]
    container = modules[first_conv_idx - 1]

    params = [x.clone() for x in conv_layer.parameters()]
    kernel_size = params[0].size()
    new_kernel_size = kernel_size[:1] + (4, ) + kernel_size[2:]
    new_kernels = params[0].data.mean(dim=1, keepdim=True).expand(new_kernel_size).contiguous()

    new_conv = nn.Conv2d(4, conv_layer.out_channels,
                         conv_layer.kernel_size, conv_layer.stride, conv_layer.padding,
                         bias=True if len(params) == 2 else False)
    
    new_conv.weight.data = new_kernels
    if len(params) == 2:
        new_conv.bias.data = params[1].data 
    layer_name = list(container.state_dict().keys())[0][:-7] 

    setattr(container, layer_name, new_conv)
    return model

def validate(model_name, split, threshold, with_softmax = True):
    
    softmax = Softmax()
    
    criterion = torch.nn.BCEWithLogitsLoss()
    val_dataset = AtlasData(split = 0, train = False, model = model_name)
    val_loader = DataLoader(val_dataset, batch_size = 1, shuffle = False)

    model = pretrainedmodels.__dict__[model_name](num_classes = 1000, pretrained = 'imagenet')
    in_features = model.last_linear.in_features
    model.last_linear = torch.nn.Linear(in_features, 28)
    
    model = construct_rgby_model(model)
    
    if model_name == 'polynet':
        model = torch.nn.DataParallel(model, device_ids = [0,1,2,3]).cuda()
        model.load_state_dict(torch.load('{}_rgby_focal_{}.pth.tar'.format(model_name, split))['state_dict'])
        model = model.eval()
    else:
        model.load_state_dict(torch.load('{}_rgby_focal_{}.pth.tar'.format(model_name, split))['state_dict'])
        model = model.eval()
        model.cuda()
        
    losses = []
    f1_scores = []
    
    y_pred = np.zeros((len(val_loader), 28))
    y = np.zeros((len(val_loader), 28))
    
    for i, (images, label_arrs, labels) in enumerate(val_loader):
        images = images.cuda()
        label_arrs_cuda = label_arrs.cuda()

        raw_predictions = model(images)
        outputs = raw_predictions.data
        
        y_pred[i, :] = raw_predictions.detach().cpu().numpy()
        y[i, :] = label_arrs.numpy()
        
        
        if with_softmax:
            raw_predictions = softmax(raw_predictions)
        
        loss = criterion(outputs, label_arrs_cuda)
        losses.append(loss)
        
        predictions = np.arange(28)[raw_predictions.data[0] > 0.15]
        
        if sum(predictions) == 0:
            prediction = np.argmax(raw_predictions.detach().cpu().numpy())
            predictions = np.zeros(28)
            np.put(predictions, prediction, 1)
        
        score = f1_score(label_arrs.numpy()[0], predictions, average = 'macro')
        f1_scores.append(score)
        
        if i%10==0:
            print('Testing {}/{}: Loss {}, Score {}:'.format(i, 
                                                             len(val_loader), 
                                                             sum(losses)/len(losses), 
                                                             sum(f1_scores)/len(f1_scores)))
    
    avg_loss = sum(losses)/len(losses)
    avg_score = sum(f1_scores)/len(f1_scores)
    print("Avg Loss", avg_loss)
    print("Avg Score", avg_score)

    return y_pred, y

# In Action

In [82]:
model_name = 'inceptionresnetv2'
threshold = 0.1

y_pred, y = validate(model_name, 0, threshold, with_softmax = False)

/home/saa2/pytorch_new/lib/python3.5/site-packages/torchvision/transforms/transforms.py:188: UserWarning: The use of the transforms.Scale transform is deprecated, please use transforms.Resize instead.
  "please use transforms.Resize instead.")


Testing 0/10449: Loss 0.09534027427434921, Score 0.8238993710691824:
Testing 10/10449: Loss 0.05150030180811882, Score 0.9268706300892761:
Testing 20/10449: Loss 0.05655095726251602, Score 0.9233882791411464:
Testing 30/10449: Loss 0.05671944096684456, Score 0.9250513449861844:
Testing 40/10449: Loss 0.057667747139930725, Score 0.9112326956104873:
Testing 50/10449: Loss 0.06324762850999832, Score 0.8892131411380176:
Testing 60/10449: Loss 0.07113557308912277, Score 0.8873142048251671:
Testing 70/10449: Loss 0.08377882838249207, Score 0.8671166132481416:
Testing 80/10449: Loss 0.08519630879163742, Score 0.8657980379781944:
Testing 90/10449: Loss 0.08844409137964249, Score 0.8514380763283694:
Testing 100/10449: Loss 0.09085726737976074, Score 0.8501211429660572:
Testing 110/10449: Loss 0.09063157439231873, Score 0.8485323657132764:
Testing 120/10449: Loss 0.09036564081907272, Score 0.8485472980962846:
Testing 130/10449: Loss 0.08873316645622253, Score 0.8514066604888513:
Testing 140/1044

Testing 1160/10449: Loss 0.09027017652988434, Score 0.8532712570265649:
Testing 1170/10449: Loss 0.09001708030700684, Score 0.853363254499653:
Testing 1180/10449: Loss 0.0901634693145752, Score 0.8530935006368561:
Testing 1190/10449: Loss 0.09003587067127228, Score 0.853411500111343:
Testing 1200/10449: Loss 0.09020041674375534, Score 0.8528580039445303:
Testing 1210/10449: Loss 0.0903109684586525, Score 0.8526128734530828:
Testing 1220/10449: Loss 0.08999823778867722, Score 0.85280206854832:
Testing 1230/10449: Loss 0.08983909338712692, Score 0.8527182805892735:
Testing 1240/10449: Loss 0.08954351395368576, Score 0.8531070881056997:
Testing 1250/10449: Loss 0.08909514546394348, Score 0.8539253117034467:
Testing 1260/10449: Loss 0.08902835100889206, Score 0.8536869011644003:
Testing 1270/10449: Loss 0.08891409635543823, Score 0.8538758940472597:
Testing 1280/10449: Loss 0.08884208649396896, Score 0.8535120513537099:
Testing 1290/10449: Loss 0.08919185400009155, Score 0.853357471338307:

Testing 2310/10449: Loss 0.08818337321281433, Score 0.8527130676535889:
Testing 2320/10449: Loss 0.08810010552406311, Score 0.8528519529358455:
Testing 2330/10449: Loss 0.08826465159654617, Score 0.8524908340241694:
Testing 2340/10449: Loss 0.08835957944393158, Score 0.8524962247812975:
Testing 2350/10449: Loss 0.08846952021121979, Score 0.852220297205778:
Testing 2360/10449: Loss 0.08863204717636108, Score 0.8516749039669077:
Testing 2370/10449: Loss 0.08859718590974808, Score 0.8516962052959782:
Testing 2380/10449: Loss 0.08849281817674637, Score 0.8519841117600762:
Testing 2390/10449: Loss 0.08842021971940994, Score 0.8520957893913734:
Testing 2400/10449: Loss 0.08841031789779663, Score 0.852021059296395:
Testing 2410/10449: Loss 0.08879156410694122, Score 0.8514700789683245:
Testing 2420/10449: Loss 0.08864593505859375, Score 0.8515331001391244:
Testing 2430/10449: Loss 0.08869348466396332, Score 0.8516733925276933:
Testing 2440/10449: Loss 0.08887746930122375, Score 0.851172768441

Testing 3460/10449: Loss 0.0880817174911499, Score 0.8508997805598641:
Testing 3470/10449: Loss 0.08802670240402222, Score 0.8511028825551441:
Testing 3480/10449: Loss 0.08816524595022202, Score 0.8509490398502895:
Testing 3490/10449: Loss 0.0880684033036232, Score 0.8510951257579229:
Testing 3500/10449: Loss 0.08813799917697906, Score 0.8510741478349877:
Testing 3510/10449: Loss 0.08812157809734344, Score 0.8510466827799638:
Testing 3520/10449: Loss 0.08811793476343155, Score 0.8511147823837754:
Testing 3530/10449: Loss 0.08818367123603821, Score 0.8510835569304571:
Testing 3540/10449: Loss 0.08824922889471054, Score 0.8509813035998631:
Testing 3550/10449: Loss 0.08825992792844772, Score 0.8511424650610498:
Testing 3560/10449: Loss 0.08823759853839874, Score 0.8510900731778686:
Testing 3570/10449: Loss 0.08822077512741089, Score 0.8508461976930316:
Testing 3580/10449: Loss 0.08824806660413742, Score 0.8507689190103651:
Testing 3590/10449: Loss 0.08811614662408829, Score 0.850908713982

...

Testing 5760/10449: Loss 0.08853055536746979, Score 0.8509272673609366:
Testing 5770/10449: Loss 0.08846801519393921, Score 0.851004187638372:
Testing 5780/10449: Loss 0.0884595513343811, Score 0.8511554835747864:
Testing 5790/10449: Loss 0.08846768736839294, Score 0.8511416659176161:
Testing 5800/10449: Loss 0.08852842450141907, Score 0.8509015682176426:
Testing 5810/10449: Loss 0.08852966129779816, Score 0.8508390743075095:
Testing 5820/10449: Loss 0.08843012899160385, Score 0.8510045626033578:
Testing 5830/10449: Loss 0.08842499554157257, Score 0.8509614336068232:
Testing 5840/10449: Loss 0.08841588348150253, Score 0.8509894713489317:
Testing 5850/10449: Loss 0.08845653384923935, Score 0.8508962079154242:
Testing 5860/10449: Loss 0.0884416475892067, Score 0.8508783252911856:
Testing 5870/10449: Loss 0.0884283035993576, Score 0.8509336496059421:
Testing 5880/10449: Loss 0.08844023197889328, Score 0.8508603762480894:
Testing 5890/10449: Loss 0.08836951851844788, Score 0.85106500902470

Testing 6910/10449: Loss 0.08913379907608032, Score 0.8496584147047427:
Testing 6920/10449: Loss 0.08919399231672287, Score 0.8495692573011008:
Testing 6930/10449: Loss 0.08932146430015564, Score 0.8493680474317923:
Testing 6940/10449: Loss 0.08934110403060913, Score 0.8492805579771197:
Testing 6950/10449: Loss 0.08933049440383911, Score 0.8493298830378565:
Testing 6960/10449: Loss 0.08925892412662506, Score 0.8494451392731529:
Testing 6970/10449: Loss 0.08921225368976593, Score 0.8494842251892852:
Testing 6980/10449: Loss 0.08914569020271301, Score 0.8496588782758929:
Testing 6990/10449: Loss 0.08921745419502258, Score 0.849593003703738:
Testing 7000/10449: Loss 0.08920937776565552, Score 0.8495718233881719:
Testing 7010/10449: Loss 0.08926095813512802, Score 0.8495518472255273:
Testing 7020/10449: Loss 0.08923804014921188, Score 0.8495403388341263:
Testing 7030/10449: Loss 0.08933805674314499, Score 0.8495046866866144:
Testing 7040/10449: Loss 0.08929099142551422, Score 0.84954329944

Testing 8060/10449: Loss 0.08986210823059082, Score 0.8491030496777213:
Testing 8070/10449: Loss 0.08987867087125778, Score 0.8490318208412544:
Testing 8080/10449: Loss 0.08990776538848877, Score 0.8490450142812537:
Testing 8090/10449: Loss 0.08987167477607727, Score 0.8490483737451011:
Testing 8100/10449: Loss 0.08992442488670349, Score 0.84902506318573:
Testing 8110/10449: Loss 0.08991752564907074, Score 0.8490923667797953:
Testing 8120/10449: Loss 0.08989305049180984, Score 0.8492064784893714:
Testing 8130/10449: Loss 0.08983825147151947, Score 0.849250888064639:
Testing 8140/10449: Loss 0.08981075882911682, Score 0.8492507241455398:
Testing 8150/10449: Loss 0.08981306105852127, Score 0.849304794729921:
Testing 8160/10449: Loss 0.08979370445013046, Score 0.8492747673389403:
Testing 8170/10449: Loss 0.0897940844297409, Score 0.8492538201161448:
Testing 8180/10449: Loss 0.08983897417783737, Score 0.8492280056361589:
Testing 8190/10449: Loss 0.08982031047344208, Score 0.849257760710506

Testing 9210/10449: Loss 0.08965987712144852, Score 0.8498607811491347:
Testing 9220/10449: Loss 0.0896289274096489, Score 0.8498617832514053:
Testing 9230/10449: Loss 0.08965566754341125, Score 0.8498207631836384:
Testing 9240/10449: Loss 0.08966926485300064, Score 0.8497750230355388:
Testing 9250/10449: Loss 0.08971651643514633, Score 0.8496799817432913:
Testing 9260/10449: Loss 0.08971928060054779, Score 0.8496986969684258:
Testing 9270/10449: Loss 0.0896778553724289, Score 0.8497367183735568:
Testing 9280/10449: Loss 0.08966820687055588, Score 0.8497657618096471:
Testing 9290/10449: Loss 0.08971521258354187, Score 0.8496680646760187:
Testing 9300/10449: Loss 0.08971575647592545, Score 0.8496617026614637:
Testing 9310/10449: Loss 0.08976401388645172, Score 0.849648974085414:
Testing 9320/10449: Loss 0.08973599225282669, Score 0.8496861896129612:
Testing 9330/10449: Loss 0.08969880640506744, Score 0.8496873670109247:
Testing 9340/10449: Loss 0.08964616805315018, Score 0.8498077065504

Testing 10350/10449: Loss 0.09020718187093735, Score 0.8487868679280888:
Testing 10360/10449: Loss 0.09018481522798538, Score 0.8488185901132932:
Testing 10370/10449: Loss 0.09015287458896637, Score 0.8489050328655506:
Testing 10380/10449: Loss 0.09014368057250977, Score 0.8488797763397224:
Testing 10390/10449: Loss 0.09019742906093597, Score 0.8488012973379423:
Testing 10400/10449: Loss 0.09021095931529999, Score 0.8487788479132793:
Testing 10410/10449: Loss 0.090220145881176, Score 0.8487139797834632:
Testing 10420/10449: Loss 0.09019351750612259, Score 0.848732865593618:
Testing 10430/10449: Loss 0.09019479155540466, Score 0.8487278164535773:
Testing 10440/10449: Loss 0.09018133580684662, Score 0.8487762183982741:
Avg Loss tensor(1.00000e-02 *
       9.0151, device='cuda:0')
Avg Score 0.8488140769316765


In [54]:
import scipy.optimize as opt

def sigmoid_np(x):
    return 1.0/(1.0 + np.exp(-x))

def F1_soft(preds,targs,th=0.5,d=50.0):
    preds = sigmoid_np(d*(preds - th))
    targs = targs.astype(np.float)
    score = 2.0*(preds*targs).sum(axis=0)/((preds+targs).sum(axis=0) + 1e-6)
    return score

def fit_val(x,y):
    params = 0.5*np.ones(28)
    wd = 1e-5
    error = lambda p: np.concatenate((F1_soft(x,y,p) - 1.0,
                                      wd*(p - 0.5)), axis=None)
    p, success = opt.leastsq(error, params)
    return p


In [67]:
pred = y_pred.max(axis = 0)

In [69]:
th = fit_val(pred, y)

In [70]:
th[th<0.1] = 0.1

In [72]:
from sklearn.metrics import f1_score

In [80]:
th_t = np.array([0.565,0.39,0.55,0.345,0.33,0.39,0.33,0.45,0.38,0.39,
               0.34,0.42,0.31,0.38,0.49,0.50,0.38,0.43,0.46,0.40,
               0.39,0.505,0.37,0.47,0.41,0.545,0.32,0.1])

f1_score(y, y_pred>0.2, average = 'macro')

0.583117071590937

In [5]:
model_name = 'se_resnext101_32x4d'
threshold = 0
suffix = 'raw'

generate_preds(model_name, threshold, suffix)

-----------------------------------------------------
00008af0-bad0-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[-15.8531, -13.2731,   5.2501,  -4.9905, -19.5272, -13.6434,
         -16.5655, -15.3984, -17.6735, -20.8465, -23.7271, -20.4197,
         -15.4198, -14.6580, -20.1054, -20.4546, -12.9255, -21.6290,
         -19.2927, -13.3953, -16.2902, -20.4457, -17.6758, -15.9690,
         -16.4154, -18.2558, -16.1826, -31.0352]], device='cuda:0')
Prediction: [2]
Number of predictions 1
00008af0-bad0-11e8-b2b8-ac1f6b6435d0
2
-----------------------------------------------------
0000a892-bacf-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[  3.0133,  -8.5014,  -6.5825,  -9.3592,  -8.7115,  -8.5797,
          -9.8073, -12.1489, -17.0327, -18.6993, -18.6823, -11.3163,
         -15.0991, -12.0184,  -9.6359, -14.4265,  -3.3913,  -5.2793,
          -4.6238,  -6.0720, -11.9128,  -7.0093, -17.9009,  -3.7688,
         -10.1397,   5.2089,  -7.0162, -18.7319]], device='cuda:0')
Prediction: [0, 25]
N

-----------------------------------------------------
00673f64-bad2-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[ -2.5446, -17.7437, -11.1860, -11.4788,  -3.5536,   0.2281,
         -14.2043, -14.1725, -21.2623, -24.9542, -25.1976,  -5.6017,
         -14.6912, -12.3445, -20.7340, -15.1850, -15.4276, -17.5308,
         -12.9257, -17.5606, -20.6100, -13.5401,  -9.7683, -21.7608,
         -12.5130,  -3.7785, -15.2554, -13.9215]], device='cuda:0')
Prediction: [5]
Number of predictions 1
00673f64-bad2-11e8-b2b8-ac1f6b6435d0
5
-----------------------------------------------------
0070171c-bad0-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[-14.3929, -12.0142, -15.7330, -15.9739, -10.3413, -20.7191,
          -5.4239, -10.7585, -29.9359, -16.5047, -23.6647, -10.4207,
          -5.0397, -14.1681,   6.5900, -27.5865, -13.6932, -11.6954,
          -7.5151, -10.9345, -22.6911,  -2.0452, -15.4648, -21.4089,
         -21.2193,  -8.2681, -26.4470, -43.5840]], device='cuda:0')
Prediction: [14]
Numb

-----------------------------------------------------
00ba25e2-bacf-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[  2.0777, -15.6736, -12.7268, -12.3138, -26.5898, -18.7681,
         -28.3437, -17.8339, -23.2977, -15.0482, -25.7671, -20.9513,
         -19.9197,  14.2322, -22.4200, -28.8233, -27.3723, -32.9811,
         -20.7160,  -8.4300, -20.9815, -26.9820, -20.1351, -15.3735,
         -27.3197, -17.4332, -26.1118, -34.8091]], device='cuda:0')
Prediction: [0, 13]
Number of predictions 2
00ba25e2-bacf-11e8-b2b8-ac1f6b6435d0
0 13
-----------------------------------------------------
00bb4f2a-bada-11e8-b2b9-ac1f6b6435d0
Raw Prediction tensor([[ -0.8936, -19.4928,   0.7248,  -7.2725, -14.3806,  -5.7904,
         -12.3718, -10.4019, -20.7101, -22.3114, -29.1461, -16.5717,
         -17.1431, -13.0639, -21.7298, -26.4155, -15.3948, -15.3426,
         -10.6398, -10.3598, -15.3393, -14.8731, -21.1566,  -3.4859,
         -18.0977,  -1.7012, -15.5844, -24.6438]], device='cuda:0')
Prediction: [2

-----------------------------------------------------
01170db6-bad4-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[  3.0865, -32.7011, -17.5462, -36.3785, -31.2504, -33.4814,
          -3.4051, -20.2225, -30.6822, -30.3537, -35.0066, -28.3148,
         -23.2654, -22.8244, -21.8239, -29.8842, -22.3756, -18.1922,
         -17.8074, -23.1520, -16.1581, -13.0184, -23.8847,  -5.2645,
         -25.7536,   1.6611, -32.9013, -34.8921]], device='cuda:0')
Prediction: [0, 25]
Number of predictions 2
01170db6-bad4-11e8-b2b8-ac1f6b6435d0
0 25
-----------------------------------------------------
01182374-bac8-11e8-b2b7-ac1f6b6435d0
Raw Prediction tensor([[-12.0871, -14.5322,   8.2087,  -7.2691, -18.5702, -10.0146,
         -17.5288, -12.5121, -14.7779, -16.9544, -21.4090, -12.9523,
         -11.8479,  -9.3215, -19.6140, -11.7485, -10.4647, -17.2515,
         -16.1597,  -9.0531, -13.9403, -14.6790, -15.6715, -13.9183,
         -12.9308, -18.1006,  -9.5979, -27.9226]], device='cuda:0')
Prediction: [2

-----------------------------------------------------
017cd0e8-bace-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[  8.5986, -16.2695,  -0.5078, -13.6242, -14.2145,  -9.6015,
         -16.4847,  -8.6906, -21.1965, -21.3069, -25.7549, -15.1964,
         -16.5125, -16.9344, -17.0941, -15.8437, -10.2596,  -5.8821,
         -13.9552, -15.3831, -15.8091, -15.9541, -17.3453, -14.4814,
         -20.7924, -15.6563, -15.0645, -17.5464]], device='cuda:0')
Prediction: [0]
Number of predictions 1
017cd0e8-bace-11e8-b2b8-ac1f6b6435d0
0
-----------------------------------------------------
017faf3e-bad3-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[-19.3516, -15.0986, -10.6244, -18.2960, -25.5902, -17.7836,
         -12.6791, -14.4650, -28.8779, -30.7061, -35.6720, -17.8015,
         -12.4068, -27.7925,  -0.8320, -35.3943, -15.6591, -11.2000,
         -16.1429, -13.3531, -22.9733, -11.1891, -19.5683, -18.2097,
         -14.1985,  -7.2056, -26.3614, -41.9972]], device='cuda:0')
No value passed the t

...

-----------------------------------------------------
fe5d131e-bad2-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[ 29.4481, -15.3323, -17.5392, -25.5230, -22.3412, -30.9528,
         -27.4600, -15.3399, -41.5385, -38.6274, -48.6967, -26.0952,
         -23.1588, -24.7480, -18.5370, -34.3191, -13.6700,  -7.9070,
         -23.1099, -13.5553, -31.4915, -23.5463, -35.9414, -24.1620,
         -37.0455, -17.5809, -27.7483, -39.2785]], device='cuda:0')
Prediction: [0]
Number of predictions 1
fe5d131e-bad2-11e8-b2b8-ac1f6b6435d0
0
-----------------------------------------------------
fe5eacfc-bacc-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[  0.9258,   2.0310,  -8.3805, -15.2409,  -5.0291, -12.3753,
         -13.6425,  -2.8783, -20.2480, -13.2475, -19.9917, -16.8508,
         -11.9392, -14.0551, -12.8839, -26.6301, -14.1049, -14.7199,
          -9.3581,   1.4524, -20.9240, -14.7204,  -5.1205, -15.0513,
         -19.3676,  -0.0730, -14.2099, -20.9950]], device='cuda:0')
Prediction: [0, 1, 19

-----------------------------------------------------
feb51386-bada-11e8-b2b9-ac1f6b6435d0
Raw Prediction tensor([[  9.5735, -12.5859,  -4.9667,  -8.1945, -10.6947,  -0.9174,
         -14.7565, -13.4269, -19.3574, -20.6337, -22.6272, -12.3724,
         -11.4171, -11.3630, -17.4784, -13.2790, -10.3047, -17.0228,
          -7.2124,  -4.3330, -11.5060, -10.1423, -13.5429,  -9.0845,
         -13.9169,  -3.4899, -13.9253, -17.7107]], device='cuda:0')
Prediction: [0]
Number of predictions 1
feb51386-bada-11e8-b2b9-ac1f6b6435d0
0
-----------------------------------------------------
febff930-bac7-11e8-b2b7-ac1f6b6435d0
Raw Prediction tensor([[ 14.0079,  -7.5116, -22.7565, -26.9139, -17.8873, -11.1005,
         -20.3635, -29.7019, -43.3435, -42.4255, -46.6741, -30.0759,
         -25.0854, -28.1878, -22.9318, -32.1942, -22.9346, -15.9441,
         -29.3672, -29.8614, -25.2810, -24.3998, -32.9593, -16.5717,
         -37.5819, -22.7572, -24.5911, -34.2575]], device='cuda:0')
Prediction: [0]
Numbe

-----------------------------------------------------
fef9f134-bad2-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[  3.7887,  -7.9336, -13.2953, -18.8345,  -9.7070,  -7.6378,
         -12.4549,  -2.1768, -22.5207, -16.5618, -17.7069, -11.5947,
         -22.5629, -21.7274, -18.2677, -20.3927, -20.3954, -19.2341,
           5.7151, -13.3041, -13.5129, -12.9963, -12.8102, -11.1206,
         -16.1888, -10.8886, -16.8784, -23.5559]], device='cuda:0')
Prediction: [0, 18]
Number of predictions 2
fef9f134-bad2-11e8-b2b8-ac1f6b6435d0
0 18
-----------------------------------------------------
fefa6a48-bacc-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[ -2.4211,  -7.4421, -11.1168, -11.4306,   1.7219,  -6.4813,
          -7.2164, -15.3447, -17.4508, -13.2921, -18.5537,  -7.4123,
          -5.4207,  -7.7437, -12.5019, -17.4187,  -5.9193, -17.9991,
          -8.2861,  -2.7565, -15.5190,  -5.2319,  -9.2094, -14.9991,
          -7.4786,   1.0009, -10.9296, -14.6556]], device='cuda:0')
Prediction: [4

-----------------------------------------------------
ff4aa9a4-bac7-11e8-b2b7-ac1f6b6435d0
Raw Prediction tensor([[ -3.7551, -12.0919, -12.3288, -14.1760, -11.3780, -15.7830,
         -11.7980,  -7.2439, -20.5912, -18.6732, -22.1381, -15.9412,
         -14.3724, -13.7302, -16.8701, -20.9809,  -9.5211,  -9.9639,
         -13.5757, -11.2036, -15.3170,  -4.7639,  -7.9892, -11.1224,
         -13.2434,   0.9739, -12.4010, -19.5114]], device='cuda:0')
Prediction: [25]
Number of predictions 1
ff4aa9a4-bac7-11e8-b2b7-ac1f6b6435d0
25
-----------------------------------------------------
ff5464dc-baca-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[ -8.9787, -18.5016, -14.3493, -21.4285, -17.4457, -10.2861,
         -16.0010,  -8.1698, -27.5946, -28.3062, -29.1822, -13.5339,
          -5.7922, -18.2350, -21.0542, -11.1840,  -3.7625, -23.6273,
         -15.7623,  -6.2709, -22.6065,   5.3676, -18.8114, -15.5667,
         -11.4926,  -2.6748, -22.7816, -25.7616]], device='cuda:0')
Prediction: [21]
Nu

-----------------------------------------------------
ffd83fa4-bacb-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[ 12.0870, -18.6297, -11.2979, -10.0256, -16.9186, -16.2189,
         -16.9736, -17.2617, -20.6582, -20.5048, -25.1723, -10.0793,
         -16.6975, -14.8614, -19.4356, -19.2940, -11.7809, -10.9651,
         -15.0529, -13.0473, -18.2717, -11.9468, -10.9257, -14.7122,
         -17.9006,  -5.9000, -17.2127, -15.6394]], device='cuda:0')
Prediction: [0]
Number of predictions 1
ffd83fa4-bacb-11e8-b2b8-ac1f6b6435d0
0
-----------------------------------------------------
ffd91122-bad0-11e8-b2b8-ac1f6b6435d0
Raw Prediction tensor([[ 14.9205, -13.7937,   1.1992, -10.0561, -13.2077, -13.0238,
         -11.1693,  -6.2290, -14.8896, -18.9782, -19.1844,  -3.4430,
         -17.1754, -14.9012, -12.0661, -16.5392, -11.0856, -14.9496,
          -9.5225, -12.0276, -13.4909,  -7.0061,  -2.7788, -10.7337,
          -3.5025,  -6.5157, -15.5206,  -9.7055]], device='cuda:0')
Prediction: [0, 2]
Nu

In [10]:
state = torch.load('polynet_0.pth.tar')

In [11]:
state['epoch'] = 34

In [12]:
torch.save(state,'polynet_0.pth.tar')

In [59]:
import pandas as pd

df_inceptionv4 = pd.read_csv('submission_015.csv')
df_resnext = pd.read_csv('submission_015_resnext.csv')
df_polynet = pd.read_csv('polynet.csv')

In [60]:
from sklearn.preprocessing import MultiLabelBinarizer

multilabel = MultiLabelBinarizer()

In [61]:
def convert_to_array(item):
    item = np.array([int(x) for x in item.split(' ')])
    return item

df_inceptionv4['Predicted'] = df_inceptionv4['Predicted'].apply(convert_to_array)
df_resnext['Predicted'] = df_resnext['Predicted'].apply(convert_to_array)
df_polynet['Predicted'] = df_polynet['Predicted'].apply(convert_to_array)

In [62]:
y_resnext = multilabel.fit_transform((df_resnext['Predicted'].values))
y_inception = multilabel.transform((df_inceptionv4['Predicted'].values))
y_polynet = multilabel.transform((df_polynet['Predicted'].values))

In [131]:
def generate_final_pred(y_inception, y_resnext, y_polynet):
    final_pred = ((1.2 * y_inception + y_resnext + 1.4 * y_polynet)/1.7).astype(int)
    
    for i in range(len(final_pred)):
        if sum(final_pred[i]) == 0:
            final_pred[i] = y_polynet[0]
            
    return final_pred


final_pred = generate_final_pred(y_inception, y_resnext, y_polynet)

In [132]:
final_preds = []

for x in final_pred:
    test = [str(i[0]) for i in np.argwhere(x)]
    
    test = ' '.join(test)
    final_preds.append(test)

In [133]:
df = pd.DataFrame()

In [134]:
df['Id'] = df_inceptionv4['Id']
df['Predicted'] = final_preds

In [135]:
df.to_csv('aggregated_1.csv', index = False)

In [130]:
df.head()

Id Predicted
0  00008af0-bad0-11e8-b2b8-ac1f6b6435d0         2
1  0000a892-bacf-11e8-b2b8-ac1f6b6435d0       0 5
2  0006faa6-bac7-11e8-b2b7-ac1f6b6435d0      0 25
3  0008baca-bad7-11e8-b2b9-ac1f6b6435d0         0
4  000cce7e-bad4-11e8-b2b8-ac1f6b6435d0         2